### install packge

In [ ]:
#import sys
#!{sys.executable} -m pip install natsort

### libs

In [1]:
import pyNN.spiNNaker as sim
import pyNN.utility.plotting as plot
import matplotlib.pyplot as plt
import numpy as np
import os, random, csv, pickle, json
from pyNN.utility.plotting import Figure, Panel
import cv2
#from elephant.spade import spade
import quantities as pq
from IPython.display import clear_output
#from natsort import natsorted
import time
import seaborn as sns
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay, classification_report

sim.setup(timestep=1,time_scale_factor=10)
#sim.set_number_of_neurons_per_core(neuron_type=p.IF_cond_exp(),max_permitted=150)
#sim.set_number_of_neurons_per_core(sim.SpikeSourceArray, neurons//8)

2022-11-03 17:12:35 INFO: Read cfg files: /home/bbpnrsoa/sPyNNaker/lib/python3.8/site-packages/spinn_front_end_common/interface/spinnaker.cfg, /home/bbpnrsoa/sPyNNaker/lib/python3.8/site-packages/spynnaker/pyNN/spynnaker.cfg, /home/bbpnrsoa/.spynnaker.cfg
2022-11-03 17:12:35 INFO: Will search these locations for binaries: /home/bbpnrsoa/sPyNNaker/lib/python3.8/site-packages/spinn_front_end_common/common_model_binaries : /home/bbpnrsoa/sPyNNaker/lib/python3.8/site-packages/spynnaker/pyNN/model_binaries
2022-11-03 17:12:35 WARNING: /home/bbpnrsoa/tools/reports has 69 old reports that have not been closed
2022-11-03 17:12:35 INFO: Setting time scale factor to 10.
2022-11-03 17:12:35 INFO: Setting machine time step to 1000 micro-seconds.


['/home/bbpnrsoa/sPyNNaker/lib/python3.8/site-packages/spinn_front_end_common/interface/spinnaker.cfg', '/home/bbpnrsoa/sPyNNaker/lib/python3.8/site-packages/spynnaker/pyNN/spynnaker.cfg', '/home/bbpnrsoa/.spynnaker.cfg']


0

In [2]:
num_classes = 2 # Number of Classes
file = "C1_P2_P1_1"
training_data_lists = [os.listdir(os.getcwd()+"/events/polarity_all/"+file+"/splits/"+str(i)+"/") for i in range(num_classes)]
training_class_lens = [len(i) for i in training_data_lists]

#classes = [i for i in range(num_classes)]
classes = list(range(num_classes)) 
print(classes)

time_per_exp = 30  # Time in ms per example #750
num_examples_seen = {c:0 for c in classes}
batch_size = 5   # Simulation for batch_size*10 examples will be done together

total_examples = sum(training_class_lens)
print(training_class_lens)
print(total_examples)
print(num_examples_seen)

[0, 1]
[384, 179]
563
{0: 0, 1: 0}


In [3]:
# Important Variables
n_excitatory_neurons = batch_size*num_classes
excitatory_neuron_parameters = {
    'v_rest':   -65.0,  # Resting membrane potential in mV.
    'cm':         1.0,  # Capacity of the membrane in nF
    'tau_m':     100.0,  # Membrane time constant in ms.
    'tau_refrac': 5.0,  # Duration of refractory period in ms.
    'tau_syn_E':  1.0,  # Decay time of the excitatory synaptic conductance in ms.
    'tau_syn_I':  2.0,  # Decay time of the inhibitory synaptic conductance in ms.
    'e_rev_E':    0.0,  # Reversal potential for excitatory input in mV
    'e_rev_I':  -100.0,  # Reversal potential for inhibitory input in mV
    'v_thresh': -52.0,  # Spike threshold in mV.
    'v_reset':  -65.0,  # Reset potential after a spike in mV.
    'i_offset':   0.0,  # Offset current in nA
}
n_inhibitory_neurons = n_excitatory_neurons # equal number of excitatory and inhibitory neurons
inhibitory_neuron_parameters = {
    'v_rest':   -40.0,  # Resting membrane potential in mV.
    'cm':         1.0,  # Capacity of the membrane in nF
    'tau_m':     10.0,  # Membrane time constant in ms.
    'tau_refrac': 2.0,  # Duration of refractory period in ms.
    'tau_syn_E':  5.0,  # Decay time of the excitatory synaptic conductance in ms.
    'tau_syn_I':  0.01,  # Decay time of the inhibitory synaptic conductance in ms.
    'e_rev_E':    0.0,  # Reversal potential for excitatory input in mV
    'e_rev_I':  -85.0,  # Reversal potential for inhibitory input in mV
    'v_thresh': -40.0,  #40 Spike threshold in mV.
    'v_reset':  -45.0,  # Reset potential after a spike in mV.
    'i_offset':   0.0,  # Offset current in nA
}

In [4]:
classss = np.random.randint(low=0,high=num_classes)
classs = classes[classss] #classs
num_exp = np.random.randint(low=0,high=training_class_lens[classs])
print("random Class is "+str(classs))
pickle_file = os.getcwd()+"/events/polarity_all/"+file+"/splits/"+str(classs)+"/"+str(training_data_lists[classs][num_exp])
print(pickle_file)
data_point = [[] for _ in range(255*720)]
with open(pickle_file, 'rb') as f:
    data_point = pickle.load(f)
print(max(max(data_point)))

random Class is 0
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/0/506.pkl
29


In [5]:
class_history = []
class_selector = []
for i in range(batch_size):
    random.shuffle(classes)
    class_selector+=classes
class_history+=list(class_selector)
print("Class History: ", class_history)

spike_array = [[] for _ in range(255*720)]

for clas in class_selector: #classs
    #data_point = ev.read_dataset(os.getcwd()+"/data/train/"+str(clas)+"/"+str(training_data_lists[clas][num_examples_seen[clas]]))
    data_point = [[] for _ in range(255*720)]
    pickle_file = os.getcwd()+"/events/polarity_all/"+file+"/splits/"+str(clas)+"/"+str(training_data_lists[clas][num_examples_seen[clas]])
    print(pickle_file)
    with open(pickle_file, 'rb') as f:
        data_point = pickle.load(f)
    
    for ii in range(len(data_point)):
        if len(data_point[ii]) > 0:
            for iii in range(len(data_point[ii])):
                data_point[ii][iii] += np.float64(time_per_exp*sum(num_examples_seen.values()))
                #print(data_point[ii][iii])
    num_examples_seen[clas]+=1
    
    idx_sa = 0
    for sa,dpsa in zip(spike_array,data_point):
        spike_array[idx_sa] = sa+dpsa
        idx_sa+=1
    
num_events=0
for i in spike_array:
    num_events+=len(i)
print("Number of events is "+str(num_events))

Class History:  [0, 1, 0, 1, 0, 1, 0, 1, 0, 1]
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/0/109.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/1/341.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/0/202.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/1/450.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/0/559.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/1/505.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/0/320.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/1/463.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/0/155.pkl
/home/bbpnrsoa/tools/events/polarity_all/C1_P2_P1_1/splits/1/447.pkl
Number of events is 71373


In [6]:
for i in range(len(spike_array)):
    if len(spike_array[i]) > 0:
        print(spike_array[i])
        #print(type(spike_array[i][0]))
        #break

[188.0]
[234.0]
[241.0]
[263.0]
[129.0]
[257.0]
[276.0]
[67.0]
[212.0]
[156.0]
[269.0]
[32.0, 147.0]
[194.0]
[229.0]
[168.0]
[13.0]
[194.0]
[162.0]
[125.0]
[291.0]
[229.0]
[156.0]
[138.0]
[147.0]
[269.0]
[19.0]
[194.0]
[7.0]
[218.0]
[252.0]
[48.0]
[296.0]
[286.0]
[129.0]
[67.0]
[2.0]
[269.0]
[188.0]
[229.0]
[241.0]
[67.0]
[182.0]
[37.0]
[156.0]
[263.0]
[241.0]
[67.0]
[200.0]
[234.0]
[194.0]
[286.0]
[162.0]
[257.0]
[281.0]
[182.0]
[62.0]
[125.0]
[212.0]
[7.0]
[205.0]
[269.0]
[43.0]
[100.0]
[296.0]
[19.0]
[188.0]
[174.0]
[79.0]
[147.0]
[67.0]
[200.0]
[2.0]
[114.0]
[162.0]
[194.0]
[269.0]
[7.0]
[291.0]
[133.0]
[168.0]
[281.0]
[212.0]
[32.0]
[67.0]
[62.0]
[286.0]
[73.0]
[229.0]
[13.0]
[174.0]
[223.0]
[37.0]
[241.0]
[62.0]
[194.0]
[67.0]
[212.0]
[95.0]
[194.0]
[286.0]
[162.0]
[32.0]
[7.0]
[168.0]
[84.0]
[156.0]
[120.0]
[268.0]
[147.0]
[13.0, 229.0]
[212.0]
[37.0]
[138.0]
[138.0]
[32.0]
[67.0]
[162.0]
[32.0]
[7.0]
[100.0]
[114.0]
[13.0]
[182.0]
[2.0]
[7.0]
[67.0]
[194.0]
[268.0]
[91.0]
[263.

In [7]:
#print(len(spike_array))
width = 720
height = 255
neurons = width*height
# input . It is the training data
inp = sim.Population(neurons,  # these number of neurons depends on spike array matrix. 34 x 34 = 1156. if you change the matrix then change the number of neurons here.
                   sim.SpikeSourceArray(spike_array), # all the efforts we did earlier was for spike_array
                   label="Input"
                  )
# excitatory
exc = sim.Population(n_excitatory_neurons,
                   sim.IF_cond_exp(**excitatory_neuron_parameters),
                   initial_values={'v': excitatory_neuron_parameters["v_rest"]}, # defining initial voltage
                   label="Excitatory"
                  )
# inhibitory
inh = sim.Population(n_inhibitory_neurons,
                   sim.IF_cond_exp(**inhibitory_neuron_parameters),
                   initial_values={'v': inhibitory_neuron_parameters["v_rest"]}, # defining initial voltage
                   label="Inhibitory"
                  )


In [8]:
# Record Spikes
inp.record("spikes") # Testing
exc.record(["spikes",'gsyn_exc', 'gsyn_inh','v'])
inh.record(["spikes",'gsyn_exc', 'gsyn_inh','v'])

In [9]:
min_weight = 1
max_weight = 4

sim.Projection(presynaptic_population = exc,
             postsynaptic_population = inh,
             connector = sim.OneToOneConnector(),
             synapse_type = sim.StaticSynapse(weight=3,delay=0.0),
             receptor_type = 'excitatory'
            )

# I -> E
i_e_connection_list = []
for i in range(n_excitatory_neurons):
    for j in range(n_inhibitory_neurons):
        if not i==j:
            i_e_connection_list.append((i,j))

sim.Projection(presynaptic_population = inh,
             postsynaptic_population = exc,
             connector = sim.FromListConnector(i_e_connection_list),
             synapse_type = sim.StaticSynapse(weight=0.0001,delay=0.1), # 0.0001
             receptor_type = 'inhibitory'
            )

# Input -> E
stdp_initial_weights = sim.RandomDistribution(distribution='normal_clipped',low=1,high=10, mu=0.5, sigma=0.3) #low=0,high=10, mu=0.5, sigma=0.3
print("Testing stdp initial weight random generator, rand value = ",str(stdp_initial_weights.next()))

timing_rule = sim.SpikePairRule(tau_plus=8.0,tau_minus=1.0, #8,1
                             A_plus=0.080,A_minus=0.020) # 80,20
    
weight_rule = sim.AdditiveWeightDependence(w_max=max_weight,w_min=min_weight)
#weight_rule = p.MultiplicativeWeightDependence(w_min=min_weight, w_max=max_weight)

stdp_model = sim.STDPMechanism(timing_dependence=timing_rule,
                            weight_dependence=weight_rule,
                            weight=stdp_initial_weights,delay=1.0)

stdp_proj = sim.Projection(presynaptic_population = inp,
             postsynaptic_population = exc,
             connector = sim.AllToAllConnector(),
             synapse_type = stdp_model,
             receptor_type = 'excitatory'
            )

Testing stdp initial weight random generator, rand value =  1.1168014016788446


In [10]:
initial_weights = stdp_proj.get(["weight"],"list", with_address=False)

In [11]:
sim.run(batch_size*num_classes*time_per_exp)

2022-11-03 17:13:27 INFO: Starting execution process
2022-11-03 17:13:27 INFO: Simulating for 300 1.0ms timesteps using a hardware timestep of 10000us
Adding Splitter selectors where appropriate
|0%                          50%                         100%|
2022-11-03 17:13:27 INFO: Time 0:00:00.008470 taken by SpynnakerSplitterSelector
Adding delay extensions as required
|0%                          50%                         100%|
2022-11-03 17:13:27 INFO: Time 0:00:00.008884 taken by DelaySupportAdder
2022-11-03 17:13:30 INFO: Time 0:00:03.240982 taken by SpallocMaxMachineGenerator
Preallocating resources for Extra Monitor support vertices
|0%                          50%                         100%|
2022-11-03 17:13:38 INFO: Time 0:00:07.851813 taken by PreAllocateResourcesForExtraMonitorSupport
Partitioning graph vertices
|0%                          50%                         100%|
Partitioning graph edges
|0%                          50%                         100%|
2022-11-

300.0

In [12]:
# Getting Weights and spikes
weights = stdp_proj.get(["weight"],"list", with_address=False)
weights_address = stdp_proj.get(["weight"],"list")
inp_spikes = inp.get_data("spikes")
exc_spikes = exc.get_data("spikes")
inh_spikes = inh.get_data("spikes")
exc_v = exc.get_data("v")
exc_ge = exc.get_data('gsyn_exc')
exc_gi = exc.get_data('gsyn_inh')
inh_v = inh.get_data("v")
inh_ge = inh.get_data('gsyn_exc')
inh_gi = inh.get_data('gsyn_inh')

Getting synaptic data between Input and Excitatory
|0%                          50%                         100%|
Getting synaptic data between Input and Excitatory
|0%                          50%                         100%|
Getting spikes for Input
|0%                          50%                         100%|
Getting spikes for Excitatory
|0%                          50%                         100%|
2022-11-03 17:16:29 WARNING: Population Excitatory is missing spike data in region 3 from the following cores: (4, 4, 4); 
Getting spikes for Inhibitory
|0%                          50%                         100%|
Getting v for Excitatory
|0%                          50%                         100%|
Getting gsyn_exc for Excitatory
|0%                          50%                         100%|
Getting gsyn_inh for Excitatory
|0%                          50%                         100%|
Getting v for Inhibitory
|0%                          50%                         100%|
Getting g

In [13]:
spikes = exc_spikes.segments[0].spiketrains
print(spikes)
spike_counts = [{i:0 for i in classes} for i in range(n_excitatory_neurons)]
print(class_history)
for i in range(n_excitatory_neurons):
    for j in list(spikes[i]):
        spike_counts[i][class_history[int(j)//time_per_exp]]+=1

tot = class_history[0:(n_excitatory_neurons)]
labels = [0]*len(tot)
for i in range(len(tot)):
    print(spike_counts[i])
    labels[i] = max(spike_counts[i], key=spike_counts[i].get)
print("Number of examples seen")
print(num_examples_seen)

print("Class history")
print(class_history[0:(n_excitatory_neurons)])

print("Labels")
print(labels)

num_labels = {i:0 for i in classes}
for i in labels:
    num_labels[i]+=1
    
print("Number of labels")
print(num_labels)

#print("Class is = "+str(clas))

"""target_names = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']
print(classification_report(class_history[0:(n_excitatory_neurons)], labels, target_names=None))
cm = confusion_matrix(class_history[0:(n_excitatory_neurons)], labels)
disp = ConfusionMatrixDisplay(confusion_matrix=cm)
disp.plot()
plt.show()"""

[<SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>, <SpikeTrain(array([], dtype=float64) * ms, [0.0 ms, 300.0 ms])>]
[0, 1, 0, 1, 0, 1, 0, 1, 0, 1]
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
{0: 0, 1: 0}
Number of examples seen
{0: 5, 1: 5}
Class history
[0, 1, 0, 1, 0, 1, 0, 1, 0, 1]
Labels
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Number of labels
{0: 10, 1: 0}


"target_names = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']\nprint(classification_report(class_history[0:(n_excitatory_neurons)], labels, target_names=None))\ncm = confusion_matrix(class_history[0:(n_excitatory_neurons)], labels)\ndisp = ConfusionMatrixDisplay(confusion_matrix=cm)\ndisp.plot()\nplt.show()"

In [ ]:
sim.end()

In [ ]:
# Plotting spikes
plot.Figure(
    plot.Panel(inp_spikes.segments[0].spiketrains,yticks=True,xticks=True,xlabel="Time"),
    plot.Panel(exc_spikes.segments[0].spiketrains,yticks=True,xticks=True,xlabel="Time"),
    plot.Panel(inh_spikes.segments[0].spiketrains,yticks=True,xticks=True,xlabel="Time"),
    plot.Panel(exc_v.segments[0].filter(name='v')[0],yticks=True,xticks=True,legend=None,ylim=(-70,-50)),
    plot.Panel(exc_v.segments[0].filter(name='v')[0],yticks=True,xticks=True,legend=None),
    plot.Panel(inh_v.segments[0].filter(name='v')[0],yticks=True,xticks=True,legend=None),
    plot.Panel(exc_ge.segments[0].filter(name='gsyn_exc')[0],yticks=True,xticks=True,legend=None),
    plot.Panel(inh_gi.segments[0].filter(name='gsyn_inh')[0],yticks=True,xticks=True,legend=None),
    plot.Panel(exc_ge.segments[0].filter(name='gsyn_exc')[0],yticks=True,xticks=True,legend=None),
    plot.Panel(inh_gi.segments[0].filter(name='gsyn_inh')[0],yticks=True,xticks=True,legend=None)
)

In [ ]:
w_diff = [i - j for i,j in zip(initial_weights,weights)]
# plt.figure()
# plt.hist(w_diff)
# plt.show()
plt.figure()
ax = sns.distplot(w_diff,axlabel="Weight Difference Distribution (Initial weight - Final Weight)")
plt.show()